In [142]:
import pandas as pd
import math
from datetime import datetime
import hvplot.pandas
import math
# load data
profile_df = pd.read_pickle('../data/portfolio_portfile.pkl')
benchmark_df = pd.read_pickle('../data/benchmark_portfolio.pkl')
portfolio_df = pd.read_pickle('../data/portfolio_data.pkl')

In [143]:
# to acoomodate the current pipe line
min_dates = benchmark_df.groupby('ticker')['date'].min()

for ticker, min_date in min_dates.items():
   benchmark_df.loc[(benchmark_df['ticker'] == ticker) & (benchmark_df['date'] != min_date), 'weight'] = float('nan')

benchmark_df['initial_weight'] = benchmark_df['weight']
# drop weight
benchmark_df = benchmark_df.drop(columns=['weight'])

In [144]:
# check if all unique ticker has an weight
count_list = benchmark_df.groupby('ticker')['initial_weight'].count().sort_values(ascending=False)
count_list[count_list != 1]


Series([], Name: initial_weight, dtype: int64)

In [145]:
update_profile_df = profile_df.copy()
update_profile_df['date'] = datetime(2021,1,10)
update_profile_df['weight'] = [50,100,200,300,400,500]
profile_df = pd.concat([profile_df, update_profile_df])


In [146]:
def calculate_pct(stock_df):
    stock_df['pct'] = stock_df.groupby(['ticker'])['close'].pct_change()


In [147]:
# step 1 pct
calculate_pct(portfolio_df)
calculate_pct(benchmark_df)

In [148]:
def return_weighted_stock_df(stock_price_df, profile_df=None):
    # TODO change later this a temporary solution
    # initialize weight if profile_df is not none
    merged_df = pd.DataFrame()
    if profile_df is not None:
        merged_df = stock_price_df.merge(profile_df[['weight', 'date', 'ticker']], on=['ticker', 'date'], how='outer')
        merged_df.sort_values(by=['date'], inplace=True)
        merged_df.rename(columns={'weight': 'initial_weight'}, inplace=True)
    else:
        merged_df = stock_price_df.copy()
    merged_df['current_weight'] = float('nan')
    merged_df['previous_weight'] = float('nan')
    df_grouped = merged_df.groupby('ticker')
    for _, group in df_grouped:
        pre_w = float('nan')
        ini_w = float('nan')
        for index, row in group.iterrows():
            cur_w = float('nan')
            # if has initial weight, the following row all use this initial weight
            if not pd.isna(row['initial_weight']):
                ini_w = row['initial_weight']
                cur_w = ini_w
            # just calculate current weight based on previous weight
            else:
                cur_w = pre_w * (1 + row['pct'])

            merged_df.loc[index, 'current_weight'] = cur_w    
            merged_df.loc[index, 'previous_weight'] = pre_w
            merged_df.loc[index, 'initial_weight'] = ini_w
            pre_w = cur_w
            
    # drop row where closing price is none
    merged_df = merged_df[~pd.isna(merged_df['close'])]
    # drop index
    return merged_df

In [149]:
# TODO consider save the weight calculation
portfolio_df = return_weighted_stock_df(portfolio_df, profile_df)
benchmark_df = return_weighted_stock_df(benchmark_df)

In [150]:
# benchmark_df[benchmark_df.ticker =='000008.XSHE']

In [151]:
## normalize all weight
def normalize_weight(stock_df):
    stock_df['current_weight'] = stock_df['current_weight'] / \
                                    stock_df.groupby('date')['current_weight'].transform('sum')

    stock_df['previous_weight'] = stock_df['previous_weight'] / \
                                    stock_df.groupby('date')['previous_weight'].transform('sum')

    stock_df['initial_weight'] = stock_df['initial_weight'] / \
                                    stock_df.groupby('date')['initial_weight'].transform('sum')


In [152]:
normalize_weight(portfolio_df)
normalize_weight(benchmark_df)

In [153]:
portfolio_df[portfolio_df.date == datetime(2021, 3, 12)]['initial_weight']

260    0.032258
258    0.064516
262    0.129032
263    0.258065
259    0.322581
261    0.193548
Name: initial_weight, dtype: float64

In [154]:
print(benchmark_df[benchmark_df.date == datetime(2021, 3, 12)]['initial_weight'].sum())
print(benchmark_df[benchmark_df.date == datetime(2021, 3, 12)]['current_weight'].sum())
print(benchmark_df[benchmark_df.date == datetime(2021, 3, 12)]['previous_weight'].sum())

1.0
1.0
1.0


In [155]:
# step 3 sector wegiht

# add sector information first
def create_sector_weight(stock_df, profile_df=None):
    # if profile_df is none assume the aggregate_sector stock info already in stock_df
    merged_df = None
    if profile_df is not None:
        merged_df = stock_df.merge(profile_df[['ticker', 'aggregate_sector']], on='ticker', how='left')
    else:
        merged_df = stock_df.copy()
    # set null to others
    merged_df['aggregate_sector'] = merged_df['aggregate_sector'].fillna('其他')
    # calculate previous_sector_weight
    merged_df['previous_sector_weight'] = merged_df['previous_weight'] / \
                                            merged_df.groupby(['date', 'aggregate_sector'])['previous_weight'].transform('sum')
    # calculate initial sectore weight
    merged_df['initial_sector_weight'] = merged_df['initial_weight'] / \
                                            merged_df.groupby(['date', 'aggregate_sector'])['initial_weight'].transform('sum')
    
    return merged_df

In [156]:
portfolio_df = create_sector_weight(stock_df = portfolio_df, profile_df = profile_df)
benchmark_df = create_sector_weight(benchmark_df)


In [157]:
# check result 
print(benchmark_df[benchmark_df.date == datetime(2021, 3, 12)].groupby('aggregate_sector')['previous_sector_weight'].sum())
print(benchmark_df[benchmark_df.date == datetime(2021, 3, 12)].groupby('aggregate_sector')['initial_sector_weight'].sum())


aggregate_sector
信息与通信    1.0
公用事业     1.0
其他       1.0
医药卫生     1.0
原料与能源    1.0
工业       1.0
消费       1.0
金融与地产    1.0
Name: previous_sector_weight, dtype: float64
aggregate_sector
信息与通信    1.0
公用事业     1.0
其他       1.0
医药卫生     1.0
原料与能源    1.0
工业       1.0
消费       1.0
金融与地产    1.0
Name: initial_sector_weight, dtype: float64


In [158]:
# check result 
print(portfolio_df[portfolio_df.date == datetime(2021, 3, 12)].groupby('aggregate_sector')['previous_sector_weight'].sum())
print(portfolio_df[portfolio_df.date == datetime(2021, 3, 12)].groupby('aggregate_sector')['initial_sector_weight'].sum())


aggregate_sector
信息与通信    1.0
医药卫生     1.0
原料与能源    1.0
工业       1.0
消费       1.0
Name: previous_sector_weight, dtype: float64
aggregate_sector
信息与通信    1.0
医药卫生     1.0
原料与能源    1.0
工业       1.0
消费       1.0
Name: initial_sector_weight, dtype: float64


In [159]:
## return define as the total return since the portfolio created
def calcualte_return(stock_df):
    stock_df['return'] = stock_df['close'] / stock_df.groupby(['ticker'])['close'].transform('first') - 1

In [160]:
calcualte_return(portfolio_df)
calcualte_return(benchmark_df)

In [161]:
def calculate_weighted_sector_return(stock_df):
    stock_df['weighted_sectore_return'] = stock_df['return'] * stock_df['initial_sector_weight']

In [162]:
calculate_weighted_sector_return(portfolio_df)
calculate_weighted_sector_return(benchmark_df)

In [163]:
## weighted return and sector weighred return 
def calculate_weighted_return(stock_df):
    stock_df['weighted_return'] = stock_df['return'] * stock_df['initial_weight']

In [164]:
# step
calculate_weighted_return(portfolio_df)
calculate_weighted_return(benchmark_df)

In [165]:
def calculate_weighted_sector_return(stock_df):
    stock_df['weighted_sector_return'] = stock_df['return'] * stock_df['initial_sector_weight']

In [166]:
calculate_weighted_sector_return(portfolio_df)
calculate_weighted_sector_return(benchmark_df)

In [167]:
## calcualte weighted pc
def calculate_weighted_pct(stock_df):
    stock_df['weighted_pct'] = stock_df['pct'] * stock_df['previous_weight']



In [168]:
def calculate_weighted_sector_pct(stock_df):
    stock_df['weighted_sector_pct'] = stock_df['pct'] * stock_df['previous_sector_weight']
    

In [169]:
calculate_weighted_sector_pct(portfolio_df)
calculate_weighted_sector_pct(benchmark_df)

In [170]:
calculate_weighted_pct(portfolio_df)
calculate_weighted_pct(benchmark_df)

In [171]:
calculate_weighted_sector_return(portfolio_df)
calculate_weighted_sector_return(benchmark_df)

In [172]:
## aggregate by date

# pct and weighted_return
# def agg_by_date(stock_df)
def agg_by_date(stock_df):
    agg_on_date_df = pd.DataFrame(stock_df.groupby('date')[['weighted_return','weighted_pct']].sum())
    agg_on_date_df.rename(columns={'weighted_return': 'return', 'weighted_pct': 'pct'}, inplace=True)
    return agg_on_date_df




In [173]:
p_total_view = agg_by_date(portfolio_df)
b_total_view = agg_by_date(benchmark_df)

In [174]:
## aggregate by sector
def agg_by_sector(stock_df):
    agg_on_sector_df = pd.DataFrame(stock_df.groupby(['aggregate_sector','date'])[['weighted_sector_return','weighted_sector_pct']].sum())
    agg_on_sector_df.rename(columns={'weighted_sector_return': 'return', 'weighted_sector_pct': 'pct'}, inplace=True)
    return agg_on_sector_df

In [175]:
p_sector_view = agg_by_sector(portfolio_df)
b_sector_view = agg_by_sector(benchmark_df)

In [200]:
def create_risk_table(portfolio_summary, benchmark_summary):
    # total risk tracking error  
    merged_df = pd.merge(portfolio_summary, benchmark_summary, on='date', how='outer', suffixes=('_p', '_b'))
    merged_df['risk_p'] = merged_df['return_p'].expanding().std() * math.sqrt(252)
    merged_df['risk_b'] = merged_df['return_b'].expanding().std() * math.sqrt(252)
    merged_df['active_return'] = merged_df['return_p'] - merged_df['return_b']
    merged_df['tracking_error'] = merged_df['active_return'].expanding().std() * math.sqrt(252)
    merged_df['date'] = merged_df.index
    # drop index
    merged_df.reset_index(drop=True, inplace=True)
    return merged_df

In [201]:
portfolio_risk_by_date_df = create_risk_table(p_total_view, b_total_view)

In [202]:
# add mkt cap
portfolio_risk_by_date_df

return_p     pct_p  return_b     pct_b    risk_p    risk_b  \
0    0.000000  0.000000  0.000000  0.000000       NaN       NaN   
1    0.012146  0.012146 -0.001934 -0.001934  0.136341  0.021705   
2    0.086830  0.074233 -0.000811  0.001125  0.746402  0.015414   
3    0.089435  0.002496  0.002535  0.003349  0.756382  0.030137   
4    0.148063  0.029363 -0.013015 -0.015511  0.970984  0.095654   
..        ...       ...       ...       ...       ...       ...   
242  0.028005 -0.071081  0.086827  0.000156  2.097631  0.886298   
243 -0.033053 -0.059582  0.067931 -0.017386  2.099052  0.884891   
244 -0.042238 -0.008112  0.069522  0.001490  2.101118  0.883542   
245 -0.073118 -0.031015  0.062056 -0.006981  2.105760  0.881986   
246 -0.029944  0.044300  0.064588  0.002384  2.106749  0.880502   

     active_return  tracking_error       date  
0         0.000000             NaN 2021-01-05  
1         0.014080        0.158046 2021-01-06  
2         0.087641        0.747127 2021-01-07  
3         0.086900        0.740979 2021-01-08  
4         0.161078        1.032423 2021-01-11  
..             ...             ...        ...  
242      -0.058822        1.856213 2022-01-04  
243      -0.100984        1.861347 2022-01-05  
244      -0.111761        1.867445 2022-01-06  
245      -0.135174        1.875959 2022-01-07  
246      -0.094532        1.880060 2022-01-10  

[247 rows x 9 columns]

In [217]:
profile_df.groupby('date')['weight'].sum()

# for i in range(1, len(portfolio_risk_by_date_df)):
#     cur_mkt = portfolio_risk_by_date_df.loc[i, 'mkt_cap']
#     if pd.isna(cur_mkt):
#         portfolio_risk_by_date_df.loc[i, 'mkt_cap'] = portfolio_risk_by_date_df.loc[i-1, 'mkt_cap'] * (1 + portfolio_risk_by_date_df.loc[i, 'pct_p'])
  

date
2021-01-05     600
2021-01-10    1550
Name: weight, dtype: int64

In [216]:
# display row where mkt_cap is not nana
portfolio_risk_by_date_df[portfolio_risk_by_date_df['mkt_cap'].notna()]

return_p  pct_p  return_b  pct_b  risk_p  risk_b  active_return  \
0       0.0    0.0       0.0    0.0     NaN     NaN            0.0   

   tracking_error       date  mkt_cap  
0             NaN 2021-01-05    600.0

In [ ]:
## aggregate by date
# step 7 aggregate (get portfolio return and pct(change of daily return))by date
def create_agg_by_date(stock_df):
    # sum up weighted return to get return 
    agg_return = stock_df.groupby(['date'])['weighted_return'].sum().reset_index()
    agg_return.rename(columns={'weighted_return':'return'}, inplace=True)

    # sum up weighted pct to get pct
    pct = stock_df[['date','pct','norm_weight','ticker']]
    pct['weighted_pct'] = pct['pct'] * pct['norm_weight']
    agg_pct = pct.groupby(['date'])['pct'].sum().reset_index()

    agg_df = pd.merge(agg_return, agg_pct, on='date', how='outer')
    return agg_df



p_perform_result = create_agg_by_date(p_stock_df)
p_perform_result

/var/folders/v5/2108rh5964q9j741wg_s8r1w0000gn/T/ipykernel_23255/2871737262.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pct['weighted_pct'] = pct['pct'] * pct['norm_weight']


date    return       pct
0   2021-01-05  0.000000  0.000000
1   2021-01-06  0.007011  0.036439
2   2021-01-07  0.047531  0.218707
3   2021-01-08  0.047111  0.013639
4   2021-01-11  0.052768  0.014559
..         ...       ...       ...
242 2022-01-04  0.363845 -0.199827
243 2022-01-05  0.306697 -0.193598
244 2022-01-06  0.331291  0.023418
245 2022-01-07  0.313726 -0.080728
246 2022-01-10  0.313262  0.110254

[247 rows x 3 columns]

In [ ]:
p_stock_df[p_stock_df.date==datetime(2022,1,4)]

ticker       date    open   close    high     low      volume  \
1452  603882.XSHG 2022-01-04  106.89   98.84  106.89   98.67   5140406.0   
1453  002709.XSHE 2022-01-04   57.64   54.64   57.87   54.29  42150916.0   
1454  600409.XSHG 2022-01-04    8.16    8.21    8.25    8.15  27288613.0   
1455  002920.XSHE 2022-01-04  139.71  131.69  140.91  131.45   5410083.0   
1456  300274.XSHE 2022-01-04  146.52  134.96  148.46  134.61  24205007.0   
1457  600415.XSHG 2022-01-04    4.80    4.89    4.90    4.78  58291943.0   

             money       pct      weight    return  norm_weight  \
1452  5.181929e+08 -0.076262   79.300385 -0.206996     0.107586   
1453  2.333429e+09 -0.028277  161.227501  0.612275     0.218735   
1454  2.237925e+08  0.007362   85.788924 -0.142111     0.116389   
1455  7.233361e+08 -0.060833  150.934097  0.509341     0.204770   
1456  3.333125e+09 -0.071291  176.533682  0.765337     0.239501   
1457  2.832956e+08  0.029474   83.304940 -0.166951     0.113019   

      weighted_return aggregate_sector display_name  
1452        -0.022270             医药卫生         金域医学  
1453         0.133926               工业         天赐材料  
1454        -0.016540            原料与能源         三友化工  
1455         0.104298            信息与通信         德赛西威  
1456         0.183299               工业         阳光电源  
1457        -0.018869               消费         小商品城

In [ ]:
mkt_cap_df =  pd.DataFrame(profile_df.groupby(['date'])['weight'].sum()).reset_index()
mkt_cap_df.rename(columns={'weight':'mkt_cap'}, inplace=True)
mkt_cap_df

date  mkt_cap
0 2021-01-05      600
1 2021-01-10     1550

In [ ]:
# get mkt adjustment (weight is the fund in a stock)
mkt_adjustment =  pd.DataFrame(profile_df.groupby(['date'])['weight'].sum()).reset_index()
mkt_adjustment.rename(columns={'weight':'mkt_cap'}, inplace=True)
merge_df = p_perform_result.merge(mkt_adjustment, on='date', how='outer')


for i in range(1, len(merge_df)):
    merge_df.loc[i, 'mkt_cap'] = merge_df.loc[i-1, 'mkt_cap'] * (1 + merge_df.loc[i, 'pct'])

# # calculate daily mkt_cap
# # initial_mkt_cap = merge_df.loc[0, 'mkt_cap']
# for i in range(1, len(merge_df)):
#     row = merge_df.loc[i]
#     if pd.isna(row['mkt_cap']):
#         merge_df.loc[i, 'mkt_cap'] = merge_df.loc[i-1, 'mkt_cap'] * (1 + merge_df.loc[i, 'pct_portfolio'])
    
# # step 8 calculate daily mkt cap

merge_df[merge_df.date < datetime(2021,1,10)]

date    return       pct     mkt_cap
0 2021-01-05  0.000000  0.000000  600.000000
1 2021-01-06  0.007011  0.036439  621.863161
2 2021-01-07  0.047531  0.218707  757.869005
3 2021-01-08  0.047111  0.013639  768.205269

In [ ]:
## agg by sector and day
p_stock_df['weight_in_sector'] = p_stock_df.groupby

ticker       date    open   close    high     low       volume  \
0     002709.XSHE 2021-01-05   32.54   33.89   34.22   31.39   59152352.0   
1     600415.XSHG 2021-01-05    5.33    5.87    5.87    5.22  180936477.0   
2     600409.XSHG 2021-01-05    9.23    9.57    9.66    9.08   82669289.0   
3     300274.XSHE 2021-01-05   76.03   76.45   80.20   75.27   51384827.0   
4     002920.XSHE 2021-01-05   85.44   87.25   87.95   84.07    3852674.0   
...           ...        ...     ...     ...     ...     ...          ...   
1477  600409.XSHG 2022-01-10    8.24    8.35    8.39    8.21   32516017.0   
1478  002920.XSHE 2022-01-10  130.36  138.43  141.96  130.11    5005400.0   
1479  002709.XSHE 2022-01-10   51.63   50.73   51.93   50.03   29821246.0   
1480  600415.XSHG 2022-01-10    4.70    4.75    4.85    4.67   39278041.0   
1481  603882.XSHG 2022-01-10   88.45   95.53   95.59   88.39    6991445.0   

             money       pct      weight    return  norm_weight  \
0     1.942406e+09       NaN  100.000000  0.000000     0.166667   
1     1.010225e+09       NaN  100.000000  0.000000     0.166667   
2     7.803391e+08       NaN  100.000000  0.000000     0.166667   
3     3.961995e+09       NaN  100.000000  0.000000     0.166667   
4     3.322598e+08       NaN  100.000000  0.000000     0.166667   
...            ...       ...         ...       ...          ...   
1477  2.699300e+08  0.015815   87.251829 -0.127482     0.121949   
1478  6.901614e+08  0.046888  158.659026  0.586590     0.221752   
1479  1.518902e+09 -0.019142  149.690174  0.496902     0.209216   
1480  1.859827e+08  0.010638   80.919932 -0.190801     0.113099   
1481  6.468392e+08  0.085692   76.644737 -0.233553     0.107123   

      weighted_return aggregate_sector display_name  
0            0.000000               工业         天赐材料  
1            0.000000               消费         小商品城  
2            0.000000            原料与能源         三友化工  
3            0.000000               工业         阳光电源  
4            0.000000            信息与通信         德赛西威  
...               ...              ...          ...  
1477        -0.015546            原料与能源         三友化工  
1478         0.130077            信息与通信         德赛西威  
1479         0.103960               工业         天赐材料  
1480        -0.021579               消费         小商品城  
1481        -0.025019             医药卫生         金域医学  

[1482 rows x 15 columns]

In [ ]:
def creaet_portfolio_return(stock_df):
    portfolio_df = stock_df.groupby(['date'])['weighted_return'].sum().reset_index()
    portfolio_df.rename(columns={'weighted_return':'portfolio_return'}, inplace=True)
    return portfolio_df

In [ ]:
portfolio_df = creaet_portfolio_return(p_stock_df)
portfolio_df

date  portfolio_return
0   2021-01-05          0.000000
1   2021-01-06          0.007011
2   2021-01-07          0.047531
3   2021-01-08          0.047111
4   2021-01-11          0.052768
..         ...               ...
242 2022-01-04          0.363845
243 2022-01-05          0.306697
244 2022-01-06          0.331291
245 2022-01-07          0.313726
246 2022-01-10          0.313262

[247 rows x 2 columns]